In [1]:
import pandas as pd
from pandas.plotting import scatter_matrix
import matplotlib.pyplot as plt
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import precision_score, recall_score, classification_report, f1_score, make_scorer
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
import numpy as np
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import GridSearchCV, ShuffleSplit, RandomizedSearchCV
from xgboost import XGBClassifier




In [2]:
data = pd.read_csv('WA_Fn-UseC_-Telco-Customer-Churn.csv')

In [3]:
data

customerID  gender  SeniorCitizen Partner Dependents  tenure  \
0     7590-VHVEG  Female              0     Yes         No       1   
1     5575-GNVDE    Male              0      No         No      34   
2     3668-QPYBK    Male              0      No         No       2   
3     7795-CFOCW    Male              0      No         No      45   
4     9237-HQITU  Female              0      No         No       2   
...          ...     ...            ...     ...        ...     ...   
7038  6840-RESVB    Male              0     Yes        Yes      24   
7039  2234-XADUH  Female              0     Yes        Yes      72   
7040  4801-JZAZL  Female              0     Yes        Yes      11   
7041  8361-LTMKD    Male              1     Yes         No       4   
7042  3186-AJIEK    Male              0      No         No      66   

     PhoneService     MultipleLines InternetService OnlineSecurity  ...  \
0              No  No phone service             DSL             No  ...   
1             Yes                No             DSL            Yes  ...   
2             Yes                No             DSL            Yes  ...   
3              No  No phone service             DSL            Yes  ...   
4             Yes                No     Fiber optic             No  ...   
...           ...               ...             ...            ...  ...   
7038          Yes               Yes             DSL            Yes  ...   
7039          Yes               Yes     Fiber optic             No  ...   
7040           No  No phone service             DSL            Yes  ...   
7041          Yes               Yes     Fiber optic             No  ...   
7042          Yes                No     Fiber optic            Yes  ...   

     DeviceProtection TechSupport StreamingTV StreamingMovies        Contract  \
0                  No          No          No              No  Month-to-month   
1                 Yes          No          No              No        One year   
2                  No          No          No              No  Month-to-month   
3                 Yes         Yes          No              No        One year   
4                  No          No          No              No  Month-to-month   
...               ...         ...         ...             ...             ...   
7038              Yes         Yes         Yes             Yes        One year   
7039              Yes          No         Yes             Yes        One year   
7040               No          No          No              No  Month-to-month   
7041               No          No          No              No  Month-to-month   
7042              Yes         Yes         Yes             Yes        Two year   

     PaperlessBilling              PaymentMethod MonthlyCharges  TotalCharges  \
0                 Yes           Electronic check          29.85         29.85   
1                  No               Mailed check          56.95        1889.5   
2                 Yes               Mailed check          53.85        108.15   
3                  No  Bank transfer (automatic)          42.30       1840.75   
4                 Yes           Electronic check          70.70        151.65   
...               ...                        ...            ...           ...   
7038              Yes               Mailed check          84.80        1990.5   
7039              Yes    Credit card (automatic)         103.20        7362.9   
7040              Yes           Electronic check          29.60        346.45   
7041              Yes               Mailed check          74.40         306.6   
7042              Yes  Bank transfer (automatic)         105.65        6844.5   

     Churn  
0       No  
1       No  
2      Yes  
3       No  
4      Yes  
...    ...  
7038    No  
7039    No  
7040    No  
7041   Yes  
7042    No  

[7043 rows x 21 columns]

In [4]:
#data.drop(columns=['customerID'], inplace=True)
data['Churn'][data['Churn'] == 'Yes'] = 1
data['Churn'][data['Churn'] == 'No'] = 0
data['TotalCharges'] = pd.to_numeric(data.TotalCharges, errors='coerce')

C:\Users\mprev\AppData\Local\Temp\ipykernel_8836\2240443310.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Churn'][data['Churn'] == 'Yes'] = 1
C:\Users\mprev\AppData\Local\Temp\ipykernel_8836\2240443310.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Churn'][data['Churn'] == 'No'] = 0


In [5]:
data.isnull().sum()

customerID           0
gender               0
SeniorCitizen        0
Partner              0
Dependents           0
tenure               0
PhoneService         0
MultipleLines        0
InternetService      0
OnlineSecurity       0
OnlineBackup         0
DeviceProtection     0
TechSupport          0
StreamingTV          0
StreamingMovies      0
Contract             0
PaperlessBilling     0
PaymentMethod        0
MonthlyCharges       0
TotalCharges        11
Churn                0
dtype: int64

In [6]:
data.dropna(inplace=True)
data2 = data.copy()

In [7]:
# Categorical feature funtions
def parse_one_hot(df, old_column):
    new_df = df.copy()
    new_columns = new_df[old_column].unique()
    if len(new_columns) > 2: 
        for column in new_columns:
            new_df[column] = 0
            new_df[column][new_df[old_column] == column] = 1
    if len(new_columns) == 2:
        new_df[new_columns[0]] = 0
        new_df[new_columns[0]][new_df[old_column] == new_columns[0]] = 1
    new_df.drop(columns=[old_column], inplace=True)
    return new_df

In [8]:
# Categorical features:
from sklearn.preprocessing import LabelEncoder

# replace yes, no
yes_columns = ['Partner', 'Dependents', 'PhoneService', 'OnlineSecurity', 'DeviceProtection', 'TechSupport' ,'StreamingTV', 'StreamingMovies', 'PaperlessBilling', 'Churn', 'OnlineSecurity', 'OnlineBackup']
for column in yes_columns:
    data[column][data[column]=='No'] = 0
    data[column][data[column]=='No internet service'] = -1
    data[column][data[column]=='Yes'] = 1

# replace gender
data['gender'][data['gender']=='Female'] = 0
data['gender'][data['gender']=='Male'] = 1

# cat enconder
data['MultipleLines'][data['MultipleLines']=='No'] = 0
data['MultipleLines'][data['MultipleLines']=='No phone service'] = 1
data['MultipleLines'][data['MultipleLines']=='Yes'] = 2

data['Contract'][data['Contract']=='Month-to-month'] = 1
data['Contract'][data['Contract']=='One year'] = 12
data['Contract'][data['Contract']=='Two year'] = 24

# one hot-enconder
#data = parse_one_hot(data, 'PaymentMethod')
#data = parse_one_hot(data, 'InternetService')
encoder = LabelEncoder()
data['PaymentMethod'] = encoder.fit_transform(data['PaymentMethod'])
data['InternetService'] = encoder.fit_transform(data['InternetService'])

C:\Users\mprev\AppData\Local\Temp\ipykernel_8836\948807078.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[column][data[column]=='No'] = 0
C:\Users\mprev\AppData\Local\Temp\ipykernel_8836\948807078.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[column][data[column]=='No internet service'] = -1
C:\Users\mprev\AppData\Local\Temp\ipykernel_8836\948807078.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[column][d

In [9]:
# numerical features
def standarize(df, numerical_features):
    scaler = StandardScaler()
    df_copy = df.copy()
    df_copy[numerical_features] = scaler.fit_transform(df_copy[numerical_features])
    return df_copy
    

In [10]:
raw_data = data.copy()
raw_data.drop(columns=['customerID'], inplace=True)
data = standarize(data, ['MonthlyCharges','TotalCharges', 'tenure'])
data

customerID gender  SeniorCitizen Partner Dependents    tenure  \
0     7590-VHVEG      0              0       1          0 -1.280248   
1     5575-GNVDE      1              0       0          0  0.064303   
2     3668-QPYBK      1              0       0          0 -1.239504   
3     7795-CFOCW      1              0       0          0  0.512486   
4     9237-HQITU      0              0       0          0 -1.239504   
...          ...    ...            ...     ...        ...       ...   
7038  6840-RESVB      1              0       1          1 -0.343137   
7039  2234-XADUH      0              0       1          1  1.612573   
7040  4801-JZAZL      0              0       1          1 -0.872808   
7041  8361-LTMKD      1              1       1          0 -1.158016   
7042  3186-AJIEK      1              0       0          0  1.368109   

     PhoneService MultipleLines  InternetService OnlineSecurity  ...  \
0               0             1                0              0  ...   
1               1             0                0              1  ...   
2               1             0                0              1  ...   
3               0             1                0              1  ...   
4               1             0                1              0  ...   
...           ...           ...              ...            ...  ...   
7038            1             2                0              1  ...   
7039            1             2                1              0  ...   
7040            0             1                0              1  ...   
7041            1             2                1              0  ...   
7042            1             0                1              1  ...   

     DeviceProtection TechSupport StreamingTV StreamingMovies Contract  \
0                   0           0           0               0        1   
1                   1           0           0               0       12   
2                   0           0           0               0        1   
3                   1           1           0               0       12   
4                   0           0           0               0        1   
...               ...         ...         ...             ...      ...   
7038                1           1           1               1       12   
7039                1           0           1               1       12   
7040                0           0           0               0        1   
7041                0           0           0               0        1   
7042                1           1           1               1       24   

     PaperlessBilling PaymentMethod  MonthlyCharges  TotalCharges  Churn  
0                   1             2       -1.161694     -0.994194      0  
1                   0             3       -0.260878     -0.173740      0  
2                   1             3       -0.363923     -0.959649      1  
3                   0             0       -0.747850     -0.195248      0  
4                   1             2        0.196178     -0.940457      1  
...               ...           ...             ...           ...    ...  
7038                1             3        0.664868     -0.129180      0  
7039                1             1        1.276493      2.241056      0  
7040                1             2       -1.170004     -0.854514      0  
7041                1             3        0.319168     -0.872095      1  
7042                1             0        1.357932      2.012344      0  

[7032 rows x 21 columns]

In [11]:
# remove useless column
data.drop(columns=['customerID'],inplace=True)

In [12]:
# stratify train test
train, test = train_test_split(data, test_size=0.2, stratify=data['Churn'], random_state=42)

full_train = train.copy()
y_train = train['Churn']
train.drop(columns=['Churn'], inplace = True)

full_test = test.copy()
y_test = test['Churn']
test.drop(columns=['Churn'], inplace = True)

In [13]:
y_train = y_train.astype(float)
cv = ShuffleSplit(n_splits = 5, test_size = 0.2, random_state = 42)

In [14]:
from sklearn.neural_network import MLPClassifier
xTrain, xValid = train_test_split(full_train, test_size=0.2, stratify=full_train['Churn'], random_state=42)

y = xTrain['Churn'].astype(float)

model = MLPClassifier(solver = 'lbfgs', max_iter = 200, learning_rate = 'adaptive', hidden_layer_sizes= (50, 30), alpha=  0.01, activation = 'tanh', random_state=42)
model.fit(xTrain.drop(columns='Churn'), y)


[[ 1.          0.          0.         ...  3.         -0.34397903
  -0.96884787]
 [ 1.          0.          0.         ...  0.         -1.49077432
  -0.56419072]
 [ 0.          0.          0.         ...  1.         -0.20603119
  -0.02594202]
 ...
 [ 1.          0.          0.         ...  1.         -1.47083006
  -0.56041857]
 [ 1.          0.          0.         ...  1.         -0.3340069
  -0.81410136]
 [ 1.          0.          1.         ...  0.          1.48424536
   1.8924955 ]]
[[-0.0739922   0.2658168   0.13682256  0.0581856  -0.20286914 -0.20288336
  -0.26062807  0.21595891  0.05963438  0.12271451 -0.28274384  0.27713771
   0.19606397 -0.16965314 -0.1876494  -0.18671783 -0.11545163  0.01460055
  -0.04013664 -0.12312634  0.06596724 -0.21261492 -0.1225864  -0.07881548
  -0.02590851  0.16818761 -0.17712274  0.00839501  0.05450314 -0.26748895
   0.06342649 -0.19431427 -0.25651858  0.26473825  0.27461479  0.18188283
  -0.11523251 -0.23728004  0.10865471 -0.03529613 -0.22290969 -0.

c:\Users\mprev\Documents\mc959\.venv\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:546: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


MLPClassifier(activation='tanh', alpha=0.01, hidden_layer_sizes=(50, 30),
              learning_rate='adaptive', random_state=42, solver='lbfgs')

In [15]:
import dice_ml
from dice_ml import Dice

In [16]:
raw_data

gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0         0              0       1          0       1            0   
1         1              0       0          0      34            1   
2         1              0       0          0       2            1   
3         1              0       0          0      45            0   
4         0              0       0          0       2            1   
...     ...            ...     ...        ...     ...          ...   
7038      1              0       1          1      24            1   
7039      0              0       1          1      72            1   
7040      0              0       1          1      11            0   
7041      1              1       1          0       4            1   
7042      1              0       0          0      66            1   

     MultipleLines  InternetService OnlineSecurity OnlineBackup  \
0                1                0              0            1   
1                0                0              1            0   
2                0                0              1            1   
3                1                0              1            0   
4                0                1              0            0   
...            ...              ...            ...          ...   
7038             2                0              1            0   
7039             2                1              0            1   
7040             1                0              1            0   
7041             2                1              0            0   
7042             0                1              1            0   

     DeviceProtection TechSupport StreamingTV StreamingMovies Contract  \
0                   0           0           0               0        1   
1                   1           0           0               0       12   
2                   0           0           0               0        1   
3                   1           1           0               0       12   
4                   0           0           0               0        1   
...               ...         ...         ...             ...      ...   
7038                1           1           1               1       12   
7039                1           0           1               1       12   
7040                0           0           0               0        1   
7041                0           0           0               0        1   
7042                1           1           1               1       24   

     PaperlessBilling  PaymentMethod  MonthlyCharges  TotalCharges Churn  
0                   1              2           29.85         29.85     0  
1                   0              3           56.95       1889.50     0  
2                   1              3           53.85        108.15     1  
3                   0              0           42.30       1840.75     0  
4                   1              2           70.70        151.65     1  
...               ...            ...             ...           ...   ...  
7038                1              3           84.80       1990.50     0  
7039                1              1          103.20       7362.90     0  
7040                1              2           29.60        346.45     0  
7041                1              3           74.40        306.60     1  
7042                1              0          105.65       6844.50     0  

[7032 rows x 20 columns]

In [17]:
d = dice_ml.Data(dataframe=raw_data, continuous_features=['MonthlyCharges', 'TotalCharges','tenure'], outcome_name='Churn')

In [18]:
# Using sklearn backend
m = dice_ml.Model(model=model, backend="sklearn")
# Using method=random for generating CFs
exp = dice_ml.Dice(d, m, method="random")

In [23]:
e1 = exp.generate_counterfactuals(raw_data.loc[raw_data['Churn']==1][1:2].drop(columns=['Churn']), total_CFs=1, desired_class=0)
e1.visualize_as_dataframe(show_only_changes=True)

100%|██████████| 1/1 [00:00<00:00,  6.70it/s]

[[  0.     0.     0.     0.     2.     1.     0.     1.     0.     0.
    0.     0.     0.     0.     1.     1.     2.    70.7  151.65]]
[[ 6.46127105e-01  1.73454587e+00  2.35916762e+00 -6.23073981e-01
  -2.06635306e-01 -9.70332393e-01 -1.17386488e+00  7.52926213e-01
  -9.79035141e-01  2.09473782e-01 -5.19279757e-01  8.98339105e-01
   8.59274546e-01 -7.08875354e-01 -5.64532740e-01 -4.48319753e-01
   9.04197923e-01 -5.80630099e-01 -1.66406410e-01 -6.01876284e-01
   5.52296624e-01 -1.32902029e+00 -3.20051477e-01 -9.03160545e-01
  -4.75623289e-01 -2.12759833e-01 -3.26567465e-01 -1.80938910e-01
   1.13715397e+00 -6.85836187e-01  1.35910944e+00 -2.62822147e-01
  -3.16132291e-01  2.47738691e-02  8.71945287e-01  3.39058170e-01
   4.90465871e-02 -1.87765131e+00  1.32308766e-01  3.15770134e-01
   6.48555354e-01 -4.44768327e-01 -1.06420509e+00  1.34364260e-01
   5.56939790e-02  4.00096057e-01  2.31352496e-01  6.61604708e-01
  -1.88949490e-01 -1.90199183e-01]
 [ 8.41830295e-01  1.05719793e+00 -6

gender  SeniorCitizen Partner Dependents  tenure PhoneService MultipleLines  \
0      0              0       0          0       2            1             0   

   InternetService OnlineSecurity OnlineBackup DeviceProtection TechSupport  \
0                1              0            0                0           0   

  StreamingTV StreamingMovies Contract PaperlessBilling  PaymentMethod  \
0           0               0        1                1              2   

   MonthlyCharges  TotalCharges  Churn  
0       70.699997    151.649994    0.0


Diverse Counterfactual set (new outcome: 0.0)
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB
<class 'int'>
BBBBBBBBBBBBBBBBBBBBBBBBB


gender SeniorCitizen Partner Dependents tenure PhoneService MultipleLines  \
0      -             -       -          -      -            -             -   

  InternetService OnlineSecurity OnlineBackup DeviceProtection TechSupport  \
0               -              -            -                -           -   

  StreamingTV StreamingMovies Contract PaperlessBilling PaymentMethod  \
0           -               -        -                -             -   

  MonthlyCharges TotalCharges Churn  
0          47.12            -     -

In [20]:
#query_instances_iris = xTrain[2:3].drop(columns=['Churn'])
#genetic_iris = exp_genetic_iris.generate_counterfactuals(query_instances_iris, total_CFs=7, desired_class=0)
#genetic_iris.visualize_as_dataframe()